In [84]:
import pandas as pd
import plotly.express as px
import json
import plotly.graph_objects as go
import dash
from dash import dcc, html


In [85]:
fires = pd.read_csv("NFDB_point_20240613.txt")

fires.info()

C:\Users\kirki\AppData\Local\Temp\ipykernel_24024\4175523138.py:1: DtypeWarning:

Columns (12,13) have mixed types. Specify dtype option on import or set low_memory=False.



<class 'pandas.core.frame.DataFrame'>
RangeIndex: 436564 entries, 0 to 436563
Data columns (total 25 columns):
 #   Column      Non-Null Count   Dtype  
---  ------      --------------   -----  
 0   FID         436564 non-null  int64  
 1   NFDBFIREID  436564 non-null  object 
 2   SRC_AGENCY  436564 non-null  object 
 3   NAT_PARK    436564 non-null  object 
 4   FIRE_ID     436399 non-null  object 
 5   FIRENAME    436561 non-null  object 
 6   LATITUDE    436564 non-null  float64
 7   LONGITUDE   436564 non-null  float64
 8   YEAR        436564 non-null  int64  
 9   MONTH       436564 non-null  int64  
 10  DAY         436564 non-null  int64  
 11  REP_DATE    432521 non-null  object 
 12  ATTK_DATE   202 non-null     object 
 13  OUT_DATE    223048 non-null  object 
 14  SIZE_HA     436564 non-null  float64
 15  CAUSE       436564 non-null  object 
 16  CAUSE2      436564 non-null  object 
 17  FIRE_TYPE   436564 non-null  object 
 18  RESPONSE    436564 non-null  object 
 19  PR

In [86]:
fire_map_data = fires[['FIRE_ID', 'SRC_AGENCY','LATITUDE', 'LONGITUDE', 'YEAR', 'SIZE_HA']]
fire_map_data = fire_map_data[(fire_map_data['YEAR'] >= 2013) & (fire_map_data['YEAR'] <= 2023)].sort_values(by='YEAR', ascending=True)
fire_map_data['SIZE_HA'] = fire_map_data['SIZE_HA'] * 100
fire_map_data['color'] = "black"
 
# re-map province abbreviations to names
province_dict = {
    'AB': 'Alberta',
    'BC': 'British Columbia',
    'MB': 'Manitoba',
    'NB': 'New Brunswick',
    'NL': 'Newfoundland and Labrador',
    'NS': 'Nova Scotia',
    'ON': 'Ontario',
    'PE': 'Prince Edward Island',
    'QC': 'Quebec',
    'SK': 'Saskatchewan',
    'YT': 'Yukon',
    'NT': 'Northwest Territories'
}

# need this for geojson
fire_map_data['SRC_AGENCY'] = fire_map_data['SRC_AGENCY'].replace(province_dict)

# add nunavut so it appears on the map
new_row = {
    'FIRE_ID': 'RANDFIRE1',
    'SRC_AGENCY': 'Nunavut',
    'LATITUDE': 50.990700, 
    'LONGITUDE': -85.060300,  
    'YEAR': 2023,
    'SIZE_HA': 1,  
    'color': "black"
}

new_row_df = pd.DataFrame([new_row])
fire_map_data = pd.concat([fire_map_data, new_row_df], ignore_index=True)

fire_map_data.head()

FIRE_ID SRC_AGENCY   LATITUDE   LONGITUDE  YEAR    SIZE_HA  color
0   RED39    Ontario  51.360800  -92.874800  2013  409.99999  black
1  EWF070    Alberta  53.808280 -115.676678  2013   20.00000  black
2  EWF072    Alberta  53.462695 -116.614260  2013    1.00000  black
3  EWF074    Alberta  53.659166 -115.987374  2013    1.00000  black
4  EWF079    Alberta  53.366917 -115.276800  2013   20.00000  black

In [87]:
fire_map_data.tail()

FIRE_ID SRC_AGENCY   LATITUDE   LONGITUDE  YEAR        SIZE_HA  \
63597        COC46    Ontario  50.990700  -85.060300  2023  147390.000000   
63598  20231080009     Quebec  45.270500  -73.267900  2023     130.115224   
63599        RED39    Ontario  51.180000  -94.311200  2023      20.000000   
63600       PWF142    Alberta  56.979133 -117.324533  2023       1.000000   
63601    RANDFIRE1    Nunavut  50.990700  -85.060300  2023       1.000000   

       color  
63597  black  
63598  black  
63599  black  
63600  black  
63601  black

In [106]:
# load geojson data for provinces
with open("canada_provinces.geojson", "r") as geo:
    mp = json.load(geo)

# take out weird outliers
fire_map_data_filtered = fire_map_data[
    (fire_map_data['LATITUDE'] >= 41) & (fire_map_data['LATITUDE'] <= 83) & 
    (fire_map_data['LONGITUDE'] >= -141) & (fire_map_data['LONGITUDE'] <= -52)
]

# create base chloropleth
fig = px.choropleth(
    fire_map_data_filtered,
    geojson=mp,
    locations='SRC_AGENCY',
    featureidkey="properties.name",
    scope='north america',
    color='color',
    color_discrete_map={"black": "#000000"},
    hover_data={
        'color':False,
        'SRC_AGENCY':False
    }
)

# changing colours and margins
fig.update_layout(
    margin={"r":0, "t":0, "l":0, "b":0},
    geo=dict(
        bgcolor='#0d0d0d'
    ),
    plot_bgcolor='#0d0d0d',
    paper_bgcolor='#0d0d0d', 
    height=900,
    width=1300,
    showlegend=False,
    dragmode=False,
    autosize=True
)

# some extra display stuff
fig.update_geos(
    showcountries=False, 
    showcoastlines=False,
    showland=False, 
    showlakes=False, 
    fitbounds="locations",
    subunitcolor='white'
)

# white borders for provinces
fig.update_traces(
    marker=dict(line=dict(color='white', width=0.15))
)

# Add scatter_geo trace for the fire locations
fig.add_trace(
    go.Scattergeo(
        lat=fire_map_data_filtered['LATITUDE'],
        lon=fire_map_data_filtered['LONGITUDE'],
        mode='markers',
        hoverinfo='skip',
        marker=dict(
            size=1,
            color='#f77b07', 
            symbol='circle',
            opacity=0.2,
        )
    )
)

fig.show(config={
    'staticPlot':True
})
